In [27]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
from __future__ import unicode_literals

import torch
from torch.jit import script, trace
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import csv
import random
import re
import os
import unicodedata
import codecs
from io import open
import itertools
import math

In [28]:
device=torch.device("cuda" if torch.cuda.is_available() else CPU)
print(device)

cuda


In [29]:
datadir="data"
def printLines(file, n=10):
    with open(file, 'rb') as datafile:
        lines=datafile.readlines()
    for line in lines[:n]:
        print(line)
printLines(os.path.join(datadir,"movie_lines.txt"))

b'L1045 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ They do not!\n'
b'L1044 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ They do to!\n'
b'L985 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ I hope so.\n'
b'L984 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ She okay?\n'
b"L925 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Let's go.\n"
b'L924 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ Wow\n'
b"L872 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Okay -- you're gonna need to learn how to lie.\n"
b'L871 +++$+++ u2 +++$+++ m0 +++$+++ CAMERON +++$+++ No\n'
b'L870 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ I\'m kidding.  You know how sometimes you just become this "persona"?  And you don\'t know how to quit?\n'
b'L869 +++$+++ u0 +++$+++ m0 +++$+++ BIANCA +++$+++ Like my fear of wearing pastels?\n'


In [30]:
# Splits each line of the file into a dictionary of fields
def loadLines(fileName, fields):
    lines= {}
    with open(fileName ,'r', encoding='iso-8859-1') as f:
        for line in f:
            values=line.split(" +++$+++ ")
            # Extract fields
            lineObj={}
            for i ,field in enumerate(fields):
                lineObj[field]=values[i]
            lines[lineObj['lineID']]=lineObj
    return lines
            

In [31]:
def loadConversation(fileName,lines,fields):
    conversations=[]
    with open(fileName,'r',encoding='iso=8859-1') as f:
        for line in f:
            values=line.split(" +++$+++ ")
            convObj={}
            for i, field in enumerate(fields):
                convObj[field]=values[i]
            linesId=eval(convObj['utteranceIDs'])
            convObj['lines']=[]
            for id in linesId:
                convObj['lines'].append(lines[id])
            conversations.append(convObj)
    return conversations
                         
                        
            
                
            

In [32]:
def extractSentencePairs(conversations):
    qa_pairs=[]
    for c in conversations:
        
        for i in range(len(c['lines'])-1):
            
            input_line=c['lines'][i]["text"].strip()
            target_line=c['lines'][i+1]["text"].strip()
            if input_line and target_line:
                qa_pairs.append((input_line, target_line))
                
    return qa_pairs

            
            

In [33]:
datafile= os.path.join(datadir,"formatted_movie_lines.txt")
delimiter= '\t'
delimiter= str(codecs.decode(delimiter,"unicode_escape"))
lines={}
conversations=[]

movie_lines_fields=["lineID", "characterID", "movieID", "character", "text"]

movie_conv_fields=["character1ID", "character2ID", "movieID", "utteranceIDs"]

lines=loadLines(os.path.join(datadir,"movie_lines.txt"),
                movie_lines_fields)

conversations=loadConversation(os.path.join(datadir,"movie_conversations.txt"),
                              lines,movie_conv_fields)




In [34]:
print(conversations[0])

{'character1ID': 'u0', 'character2ID': 'u2', 'movieID': 'm0', 'utteranceIDs': "['L194', 'L195', 'L196', 'L197']\n", 'lines': [{'lineID': 'L194', 'characterID': 'u0', 'movieID': 'm0', 'character': 'BIANCA', 'text': 'Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\n'}, {'lineID': 'L195', 'characterID': 'u2', 'movieID': 'm0', 'character': 'CAMERON', 'text': "Well, I thought we'd start with pronunciation, if that's okay with you.\n"}, {'lineID': 'L196', 'characterID': 'u0', 'movieID': 'm0', 'character': 'BIANCA', 'text': 'Not the hacking and gagging and spitting part.  Please.\n'}, {'lineID': 'L197', 'characterID': 'u2', 'movieID': 'm0', 'character': 'CAMERON', 'text': "Okay... then how 'bout we try out some French cuisine.  Saturday?  Night?\n"}]}


In [35]:


with open(datafile,'w',encoding='utf-8') as outputfile:
    writer=csv.writer(outputfile, delimiter=delimiter, lineterminator='\n')
    for pair in extractSentencePairs(conversations):
        writer.writerow(pair)

printLines(datafile)
        


b"Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again.\tWell, I thought we'd start with pronunciation, if that's okay with you.\r\n"
b"Well, I thought we'd start with pronunciation, if that's okay with you.\tNot the hacking and gagging and spitting part.  Please.\r\n"
b"Not the hacking and gagging and spitting part.  Please.\tOkay... then how 'bout we try out some French cuisine.  Saturday?  Night?\r\n"
b"You're asking me out.  That's so cute. What's your name again?\tForget it.\r\n"
b"No, no, it's my fault -- we didn't have a proper introduction ---\tCameron.\r\n"
b"Cameron.\tThe thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.\r\n"
b"The thing is, Cameron -- I'm at the mercy of a particularly hideous breed of loser.  My sister.  I can't date until she does.\tSeems like she could get a date easy enough...\r\n"
b'Why?\tUnsolved myster

In [36]:
# Default word tokens
PAD_token = 0  # Used for padding short sentences
SOS_token = 1  # Start-of-sentence token
EOS_token = 2  # End-of-sentence token

In [37]:
corpus_name = "cornell movie-dialogs corpus"

class Voc:
    def __init__(self,name):
        self.name=name
        self.trimmed=False
        self.word2index={}
        self.word2count={}
        self.index2word={PAD_token:"PAD",SOS_token:"SOS",EOS_token:"EOS"}
        self.num_words=3
    
    def addSentence(self,sentence):
        for word in sentence.split(" "):
            self.addWord(word)
    
    def addWord(self,word):
        if word not in self.word2index:
            self.word2index[word]=self.num_words
            self.word2count[word]=1
            self.index2word[self.num_words]=word
            self.num_words+=1
        else:
            self.word2count[word]+=1
    
    def trim(self,min_count):
        if self.trimmed:
            return
        self.trimmed=True
        keep_words=[]
        
        for k, v in self.word2count.items():
            if v>=min_count:
                keep_words.append(k)
                
        print('keep_words {} / {} ={:.4f}'.format(len(keep_words),
                                                  len(self.word2index),
                                            len(keep_words)/len(self.word2index)))
        
        self.word2index={}
        self.word2count={}
        self.index2word={PAD_token:"PAD",SOS_token:"SOS",EOS_token:"EOS"}
        self.num_words=3
        
        for word in keep_words:
            self.addWord(word)
            
        
    
        

In [40]:
MAX_LENGTH=10
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD',s)
        if unicodedata.category(c) != 'Mn'
        )

def normalizeString(s):
    s=unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s= re.sub(r"[^a-zA-Z.!?]+", r" ", s)
    s= re.sub(r"\s+", r" ", s).strip()
    return s

def readVocs(datafile,corpus_name):
    print("Reading Lines... ")
    lines= open(datafile, encoding='utf-8').read().strip().split('\n')
    pairs= [[normalizeString(s) for s in l.split('\t')] for l in lines]
    
    voc=Voc(corpus_name)
    return voc, pairs

def filterPair(p):
    return len(p[0].split(' '))<MAX_LENGTH and len(p[1].split(' '))<MAX_LENGTH

def filterPairs(pairs):
    return [pair for pair in pairs if filterPair(pair)]

def loadPrepareData(datafile, save_dir):
    print("Start preparing training data ...")
    
    voc,pairs=readVocs(datafile,corpus_name)
    print("Read {!s} sentence pairs".format(len(pairs)))
    pairs= filterPairs(pairs)
    
    for pair in pairs:
        voc.addSentence(pair[0])
        voc.addSentence(pair[1])
        
    print("counted words ", voc.num_words)
    return voc,pairs




    
    
    
    

In [41]:
# Load/Assemble voc and pairs
save_dir = os.path.join("data", "save")
voc, pairs = loadPrepareData( datafile, save_dir)
# Print some pairs to validate
print("\npairs:")
for pair in pairs[:10]:
    print(pair)

Start preparing training data ...
Reading Lines... 
Read 221282 sentence pairs
counted words  18008

pairs:
['there .', 'where ?']
['you have my word . as a gentleman', 'you re sweet .']
['hi .', 'looks like things worked out tonight huh ?']
['you know chastity ?', 'i believe we share an art instructor']
['have fun tonight ?', 'tons']
['well no . . .', 'then that s all you had to say .']
['then that s all you had to say .', 'but']
['but', 'you always been this selfish ?']
['do you listen to this crap ?', 'what crap ?']
['what good stuff ?', 'the real you .']


In [43]:
MIN_COUNT=3

def trim_rare_words(voc,pairs,MIN_COUNT):
    voc.trim(MIN_COUNT)
    keep_pairs=[]
    
    for pair in pairs:
        input_sentence=pair[0]
        output_sentence=pair[1]
        keep_input=True
        keep_output=True
        
        for word in input_sentence.split(" "):
            if word not in voc.word2index:
                keep_input=False
                break
        for word in output_sentence.split(" "):
            if word not in voc.word2index:
                keep_output=False
                break
                
        if keep_input and keep_output:
            keep_pairs.append(pair)
            
    print('keep_pairs {} / {} ={:.4f}'.format(len(keep_pairs),
                                                  len(pairs),
                                            len(keep_pairs)/len(pairs)))
    return keep_pairs


pairs=trim_rare_words(voc,pairs,MIN_COUNT)

keep_pairs 53165 / 53165 =1.0000


In [63]:
def indexesFromSentence(voc,sentence):
    return [voc.word2index[word] for word in sentence.split(" ") ]+[EOS_token]

def zeroPadding(l, fillvalue=PAD_token):
    return list(itertools.zip_longest(*l,fillvalue=fillvalue))

def binaryMatrix(l, value=PAD_token):
    m=[]
    for i ,seq in enumerate(l):
        m.append([])
        for token in seq:
            if token ==PAD_token:
                m[i].append(0)
            else:
                m[i].append(1)
                
    return m

                
                
                
                
                

In [45]:
def inputVar(l,voc):
    indexes_batch=[indexexfromSentence(voc,sentence) for sentence in l]
    lengths= torch.tensor([len(indexes) for indexes in indexes_batch ])
    padList= zeroPadding(indexes_batch)
    padVar= torch.LongTensor(padList)
    return padVar, lengths

def outputVar(l,voc):
    indexes_batch=[indexexfromSentence(voc,sentence) for sentence in l]
    max_target_lenght=max([len(indexes) for indexes in indexes_batch ])
    padList=zeroPadding(indexes_batch)
    mask=binaryMatrix(padList)
    mask=torch.ByteTensor(mask)
    padVar=torch.LongTensor(padList)
    return padVar,mask,max_target_lenght

def batch2TrainData(voc,pair_batch):
    pair_batch.sort(key=lambda x: len(x[0].split(" ")),reverse=True)
    
    input_batch=[]
    output_batch=[]
    
    for pair in pair_batch:
        input_batch.append(pair[0])
        output_batch.append(pair[1])
    
    inp,lenghts= inputVar(input_batch, voc)
    output ,mask, max_target_len = outputVar(output_batch,voc)
    return inp ,lenghts, output , mask , max_target_len

small_batch_size=5
batches= batch2TrainData(voc, [random.choice(pairs) for _ in range(small_batch_size)] )

input_variable, lengths, target_variable, mask, max_target_len = batches

print("input_variable:", input_variable)
print("lengths:", lengths)
print("target_variable:", target_variable)
print("mask:", mask)
print("max_target_len:", max_target_len)
    




input_variable: tensor([[ 101,  101,  100,  318,  219],
        [ 247,  290,   35, 2387,    6],
        [ 117,  723,    4,    4,    2],
        [ 547,    4,    2,    2,    0],
        [ 170,    2,    0,    0,    0],
        [   4,    0,    0,    0,    0],
        [   2,    0,    0,    0,    0]])
lengths: tensor([7, 5, 4, 4, 3])
target_variable: tensor([[ 147,   25,  131,   47,  196],
        [  47,  197,   76,    7,    4],
        [   7,  117,   17,    8,  188],
        [  24,   24,   51,  208,  510],
        [   6,    4,    4, 5950,    4],
        [   2,    2,    2,    6,    2],
        [   0,    0,    0,    2,    0]])
mask: tensor([[1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [1, 1, 1, 1, 1],
        [0, 0, 0, 1, 0]], dtype=torch.uint8)
max_target_len: 7


In [46]:
class EncoderRNN(nn.Module):
    def __init__(self, hidden_size,embedding, n_layers=1,dropout=0.1):
        super(EncoderRNN, self).__init__()
        self.n_layer=n_layers
        self.hidden_size= hidden_size
        self.embedding =embedding
        
        self.gru=nn.GRU(hidden_size,hidden_size, n_layers,
                        dropout=(0 if n_layers ==1 else dropout),
                        bidirectional =True)
    
    #input size (max_length, batch_size)
    #input lengths (batch size)
    # Hidden (n_layers*num_directions ,batch_size, hidden_size)
    
    def forward(self , input_seq, input_lengths, hidden=None):
        embedded=self.embedding(input_seq)
        packed=torch.nn.utils.rnn.pack_padded_sequence(embedded, input_lengths)
        outputs, hidden =self.gru(packed, hidden)
        outputs,_= torch.nn.utils.rnn.pad_packed_sequence(outputs)
        outputs=outputs[:,: ,:self.hidden_size]+ outputs[:,:,self.hidden_size:]
        return outputs, hidden
    
    # output size(max_length, batch_size, hidden_size)
    # hidden size((n_layers x num_directions, batch_size, hidden_size))
    

    
    
        
        

In [47]:
class Attn(nn.Module):
    def __init__(self,method, hidden_size):
        super(Attn,self).__init__()
        
        self.method=method
        if self.method not in ['dot', 'general','concat']:
            raise ValueError(self.method,"its not an an appropriate attention method")
        self.hidden_size= hidden_size
        if self.method=='general' :
            self.attn = torch.nn.Linear(self.hidden_size,self.hidden_size)
        elif self.method=='concat':
            self.attn= torch.nn.Linear(self.hidden_size*2,self.hidden_size)
            self.v= torch.nn.Parameter(torch.FloatTensor(hidden_size))
            
    def dot_score(self ,hidden, encoder_output):
        return torch.sum(hidden*encoder_output, dim=2)

    def general_score(self ,hidden, encoder_output):
        energy=self.attn(encoder_output)

        return torch.sum(hidden,energy, dim=2) 

    def concat_score(self ,hidden, encoder_output):
        energy= self.attn(torch.cat((hidden.expand(encoder_output.size(0),-1,-1 ),
                                     encoder_output),2)).tanh()
        return torch.sum(self.v*energy, dim=2)

    def forward(self,hidden ,encoder_outputs):

        if self.method == 'general':
            attn_energies = self.general_score(hidden, encoder_outputs)
        elif self.method == 'concat':
            attn_energies = self.concat_score(hidden, encoder_outputs)
        elif self.method == 'dot':
            attn_energies = self.dot_score(hidden, encoder_outputs)

        attn_energies=attn_energies.t()
        return F.softmax(attn_energies,dim=1).unsqueeze(1)

            
    
            

            
            

In [48]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, attn_model, embedding, hidden_size, output_size,
                 n_layers=1,dropout=0.1):
        super(AttnDecoderRNN,self).__init__()
        
        self.attn_model = attn_model
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.n_layers = n_layers
        self.dropout = dropout
        
        self.embedding =embedding
        self.embedding_dropout=nn.Dropout(dropout)
        self.gru =nn.GRU(hidden_size,hidden_size, n_layers, 
                         dropout=(0 if n_layers==1 else dropout))
        self.concat =nn.Linear(hidden_size*2,hidden_size)
        self.out=nn.Linear(hidden_size,output_size)
        self.attn=Attn(self.attn_model,hidden_size)
        
        
    def forward(self, input_step,last_hidden, encoder_outputs ):
        # Note: we run this one step (word) at a time
        # Get embedding of current input word
        
        embedded = self.embedding(input_step)
        embeddedd=self.embedding_dropout(embedded)
        
        rnn_output,hidden=self.gru(embedded,last_hidden)
        attn_wieghts=self.attn(rnn_output,encoder_outputs)
        
        context=attn_wieghts.bmm(encoder_outputs.transpose(0,1))
        rnn_output=rnn_output.squeeze(0)
        context =context.squeeze(1)
        concat_input=torch.cat((rnn_output,context),1)
        concat_output=torch.tanh(self.concat(concat_input))
        
        output=self.out(concat_output)
        output=F.softmax(output,dim=1)
        
        return output,hidden
    
        
        
        
        
        
            
            

In [49]:
def maskNLLLoss(inp, target, mask):
    nTotal = mask.sum()
    crossEntropy = -torch.log(torch.gather(inp, 1, target.view(-1, 1)))
    loss = crossEntropy.masked_select(mask).mean()
    loss = loss.to(device)
    return loss, nTotal.item()

In [50]:
def train(input_variable,lenghts,target_variable,mask,max_target_len, encoder,
         decoder,embedding, encoder_optimizer,decoder_optimizer,batchsize,
         clip,max_lenght=MAX_LENGTH):
    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()
    
    input_variable=input_variable.to(device)
    lenghts=lenghts.to(device)
    target_variable=target_variable.to(device)
    mask=mask.to(device)
    
    loss=0
    print_losses=[]
    n_totals=0
    
    encoder_outputs,encoder_hidden=encoder(input_variable,lenghts)
    decoder_input=torch.LongTensor([[SOS_token for _ in range(batch_size)]])
    decoder_input =decoder_input.to(device)
    
    decoder_hidden=encoder_hidden[:decoder.n_layers]
    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False
    
    if use_teacher_forcing:
        for t in range(max_target_len):
            decoder_output,decoder_hidden=decoder(decoder_input,decoder_hidden,
                                                 encoder_outputs)
            decoder_input=target_variable[t].view(1,-1)
            
            mask_loss, nTotal=maskNLLLoss(decoder_output, target_variable[t],mask[t])
            loss+=mask_loss
            print_losses.append(mask_loss.item()*nTotal)
            n_totals+= nTotal
    else:
        for t in range(max_target_len):
            decoder_output,decoder_hidden=decoder(decoder_input,decoder_hidden,encoder_outputs)
            _,topi=decoder_output.topk(1)
            decoder_input=torch.LongTensor([[topi[i][0] for i in range(batch_size)]])
            decoder_input =decoder_input.to(device)
            
            mask_loss,n_total =maskNLLLoss(decoder_output,target_variable[t],mask[t])
            loss+=mask_loss
            print_losses.append(mask_loss.item()*n_total)
            n_totals+= nTotal
            
            
    loss.backward()
    _=torch.nn.utils.clip_grad_norm_(encoder.parameters(),clip)
    _=torch.nn.utils.clip_grad_norm_(decoder.parameters(),clip)
    
    encoder_optimizer.step()
    decoder_optimizer.step()
    
    return sum(print_losses)/n_totals

            
            
            
    

In [51]:
def trainIters(model_name, voc, pairs, encoder, decoder ,encoder_optimizer,
             decoder_optimizer,embedding,encoder_n_layers,decoder_n_layers,save_dir,n_iterations,
             batch_size,print_every,save_every,clip,corpus_name,loadFilename):
    
    training_batches=[batch2TrainData(voc,[random.choice(pairs) for _ in range(batch_size)]) for _ in range(n_iterations)]
    
    print("INITIALIZING....." )
    start_iteration=1
    print_loss=0
    if loadFilename:
        start_iteration=checkpoint['iteration']+1
    
    for iteration in range(start_iteration,n_iterations+1):
        training_batch=training_batches[iteration -1]
        input_variable, lengths, target_variable, mask, max_target_len = training_batch
        
        loss = train(input_variable, lengths, target_variable, mask, max_target_len, encoder,
                     decoder, embedding, encoder_optimizer, decoder_optimizer, batch_size, clip)
        print_loss += loss
        
        if iteration % print_every == 0:
            print_loss_avg = print_loss / print_every
            print("Iteration: {}; Percent complete: {:.1f}%; Average loss: {:.4f}".format(iteration, iteration / n_iteration * 100, print_loss_avg))
            print_loss = 0
            
        if iteration % save_every == 0:
            directory=os.path.join(save_dir,model_name,corpus_name, 
                                   '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size))
            
            if not os.path.exists(directory):
                os.makedirs(directory)
            
            torch.save({
                'iteration': iteration,
                'en': encoder.state_dict(),
                'de': decoder.state_dict(),
                'en_opt': encoder_optimizer.state_dict(),
                'de_opt': decoder_optimizer.state_dict(),
                'loss': loss,
                'voc_dict': voc.__dict__,
                'embedding': embedding.state_dict()
                
            },os.path.join(directory, '{}_{}.tar'.format(iteration, 'checkpoint')))
            
            
            
        
        
        

In [66]:
class GreedySearchDecoder(nn.Module):
    def __init__(self,encoder,decoder):
        super(GreedySearchDecoder,self).__init__()
        self.encoder=encoder
        self.decoder=decoder
        
    def forward(self, input_seq,input_length, max_length):
        encoder_outputs,encoder_hidden=self.encoder(input_seq,input_length)
        decoder_hidden=encoder_hidden[:decoder.n_layers]
        
        decoder_input=torch.ones(1,1,device=device,dtype=torch.long)*SOS_token
        all_tokens=torch.zeros([0],device=device,dtype=torch.long)
        all_scores=torch.zeros([0],device=device)
        
        for _ in range(max_length):
            decoder_output, decoder_hidden=self.decoder(decoder_input,
                                                        decoder_hidden,
                                                        encoder_outputs)
            decoder_scores, decoder_input =torch.max(decoder_output,dim=1)
            all_tokens = torch.cat((all_tokens, decoder_input), dim=0)
            all_scores = torch.cat((all_scores, decoder_scores), dim=0)
            # Prepare current token to be next decoder input (add a dimension)
            decoder_input = torch.unsqueeze(decoder_input, 0)
            
        return all_tokens, all_scores
            
            
            
            
            
            
            
            
            
            
        
        

In [68]:
def evaluate(encoder,decoder,searcher, voc, sentence,max_length=MAX_LENGTH):
    indexes_batch=[indexesFromSentence(voc,sentence)]
    lengths = torch.tensor([len(indexes) for indexes in indexes_batch]).to(device)
    input_batch=torch.LongTensor(indexes_batch).transpose(0,1).to(device)
    
    tokens,scores=searcher(input_batch,lengths,max_length)
    
    decoded_words=[voc.index2word[token.item()] for token in tokens]
    
    return decoded_words

def evaluateInput(encoder,decoder,searcher,voc):
    input_sentence =''
    while(1):
        try:
            input_sentence=input('> ')
            if input_sentence=='q' or input_sentence=='quit' : break
                
            input_sentence=normalizeString(input_sentence)
            output_words= evaluate(encoder,decoder,searcher,voc,input_sentence)

            output_words[:] = [x for x in output_words if not (x == 'EOS' or x == 'PAD')]
            print('Bot:', ' '.join(output_words))
            
        except KeyError:
            print("Error: Encounterd unknown word")
            
    
    
    
    
    

In [54]:
# Configure models
model_name = 'cb_model'
attn_model = 'dot'
#attn_model = 'general'
#attn_model = 'concat'
hidden_size = 500
encoder_n_layers = 2
decoder_n_layers = 2
dropout = 0.1
batch_size = 64

# Set checkpoint to load from; set to None if starting from scratch
loadFilename = None
checkpoint_iter = 4000
#loadFilename = os.path.join(save_dir, model_name, corpus_name,
#                            '{}-{}_{}'.format(encoder_n_layers, decoder_n_layers, hidden_size),
#                            '{}_checkpoint.tar'.format(checkpoint_iter))


# Load model if a loadFilename is provided
if loadFilename:
    # If loading on same machine the model was trained on
    checkpoint = torch.load(loadFilename)
    # If loading a model trained on GPU to CPU
    #checkpoint = torch.load(loadFilename, map_location=torch.device('cpu'))
    encoder_sd = checkpoint['en']
    decoder_sd = checkpoint['de']
    encoder_optimizer_sd = checkpoint['en_opt']
    decoder_optimizer_sd = checkpoint['de_opt']
    embedding_sd = checkpoint['embedding']
    voc.__dict__ = checkpoint['voc_dict']
    
    
print('Building encoder and decoder ...')

embedding=nn.Embedding(voc.num_words,hidden_size)
if loadFilename:
    embedding.load_state_dict(embedding_sd)
encoder=EncoderRNN(hidden_size,embedding, encoder_n_layers,dropout)
decoder=AttnDecoderRNN(attn_model, embedding, hidden_size, voc.num_words, decoder_n_layers, dropout)
if loadFilename:
    encoder.load_state_dict(encoder_sd)
    decoder.load_state_dict(decoder_sd)
# Use appropriate device
encoder = encoder.to(device)
decoder = decoder.to(device)
print('Models built and ready to go!')
    




Building encoder and decoder ...
Models built and ready to go!


In [71]:
clip = 50.0
teacher_forcing_ratio = 1.0
learning_rate = 0.001
decoder_learning_ratio = 5.0
n_iteration = 4000
print_every = 1
save_every = 500

encoder.train()
decoder.train()

print('Building optimizers ...')
encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate * decoder_learning_ratio)

if loadFilename:
    encoder_optimizer.load_state_dict(encoder_optimizer_sd)
    decoder_optimizer.load_state_dict(decoder_optimizer_sd)
    
print("Starting Training!")
trainIters(model_name, voc, pairs, encoder, decoder, encoder_optimizer, decoder_optimizer,
           embedding, encoder_n_layers, decoder_n_layers, save_dir, n_iteration, batch_size,
           print_every, save_every, clip, corpus_name, loadFilename)
    


Building optimizers ...
Starting Training!
INITIALIZING.....


..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch

Iteration: 1; Percent complete: 0.0%; Average loss: 2.2705


..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch

Iteration: 2; Percent complete: 0.1%; Average loss: 2.6274


...

Iteration: 3998; Percent complete: 100.0%; Average loss: 3.3937


..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch

Iteration: 3999; Percent complete: 100.0%; Average loss: 3.7837


..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch.bool instead.
..\aten\src\ATen\native\cuda\LegacyDefinitions.cpp:66: UserWarning: masked_select received a mask with dtype torch.uint8, this behavior is now deprecated,please use a mask with dtype torch

Iteration: 4000; Percent complete: 100.0%; Average loss: 3.7008


In [69]:
encoder.eval()
decoder.eval()

# Initialize search module
searcher = GreedySearchDecoder(encoder, decoder)

In [70]:
evaluateInput(encoder, decoder, searcher, voc)


> how are you
Bot: i m sorry .
> Hi
Bot: hello .
> what is today?
Bot: i m not playing .
> why?
Bot: i don t know .
> what the fuck
Bot: what do you mean ?
> hehe
Error: Encounterd unknown word
> tell me something i dont know
Error: Encounterd unknown word
> tell me something i don't know
Bot: you know what i mean
> please
Bot: i m not going to die .
> please
Bot: i m not going to die .
> what are you doing
Bot: i m not going to die .
> what the fuck
Bot: what do you mean ?
> is there a place?
Bot: yeah .
> hmm
Bot: you re a good man .
> yoyo
Error: Encounterd unknown word
> yo
Bot: what ?
> exit
Bot: you re a friend of authority ?
> hmm
Bot: you re a good man .
> quit
